*this notebook requires a working PyTorch GPU environment* 

# Stable Diffusion Text to Image model

In [1]:
!pip install transformers diffusers accelerate ipywidgets

In [2]:
import torch
from diffusers import StableDiffusionPipeline
from matplotlib import pyplot as plt
import datetime

2023-09-27 13:15:44.716139: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [3]:
# diffusers docs: https://huggingface.co/docs/diffusers/api/pipelines/stable_diffusion/text2img#texttoimage-generation
# model_id = "dreamlike-art/dreamlike-diffusion-1.0"
# model_id = "prompthero/openjourney"
model_id = "XpucT/Deliberate"

In [4]:
pipe = StableDiffusionPipeline.from_pretrained(model_id, torch_dtype=torch.float16, safety_checker=None)
device = "cuda" if torch.cuda.is_available() else "mps" if torch.backends.mps.is_available() else "cpu"
pipe = pipe.to(device)

text_encoder/model.safetensors not found


Loading pipeline components...:   0%|          | 0/6 [00:00<?, ?it/s]

/opt/conda/lib/python3.10/site-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(
You have disabled the safety checker for <class 'diffusers.pipelines.stable_diffusion.pipeline_stable_diffusion.StableDiffusionPipeline'> by passing `safety_checker=None`. Ensure that you abide to the conditions of the Stable Diffusion license and do not expose unfiltered results in services or applications open to the public. Both the diffusers team and Hugging Face strongly recommend to keep the safety filter enabled in all public facing circumstances, disabling it only for use-cases that involve analyzing network behavior or auditing its results. For more information, please have a look at https://github.com/huggingface/diffusers/pull/254 .


In [11]:
import numpy as np
import ipywidgets as widgets
from IPython.display import clear_output, display

import matplotlib.pyplot as plt
from IPython.display import set_matplotlib_formats
%matplotlib inline
#set_matplotlib_formats('svg')

np.random.seed(42)

#prompt = "Renaissance-style portrait of an astronaut in space, detailed starry background, reflective helmet, matte painting, hyperdetailed, CGSociety"
#negative_prompt = "gold"
#textarea
std_layout = widgets.Layout(width="auto")

prompt_box = widgets.Textarea(value='', placeholder='cats, sharks, ships, underwater, cinematic composition', description='', layout=widgets.Layout(height="50px", width="auto"))
neg_prompt_box = widgets.Textarea(value='', placeholder='negative prompt', description='', layout=widgets.Layout(height="30px", width="auto"))
#slider 
img2gen_lab = widgets.Label(value="Images to Generate:", layout=std_layout)
img2gen_var = widgets.IntSlider(value=1, min=1, max=10, layout=std_layout)
#input
size_x_lab = widgets.Label(value="Image Width:", layout=std_layout)
size_x_var = widgets.BoundedIntText(value=32, min=32, max=512, step=8, layout=std_layout)
size_y_lab = widgets.Label(value="Image heigth:", layout=std_layout)
size_y_var = widgets.BoundedIntText(value=32, min=32, max=512, step=8, layout=std_layout)
steps_lab = widgets.Label(value="Steps:", layout=std_layout)
steps_var = widgets.BoundedIntText(value=50, min=11, max=100, step=1, layout=std_layout)
#Button
btn = widgets.Button(description="Generate", tooltip="Click me",
    layout=widgets.Layout(width="auto", height="30px", margin="30px"))
#Canvas
fig = plt.figure(figsize=(128/80, 128/80))
box = widgets.VBox([prompt_box, neg_prompt_box, img2gen_lab, img2gen_var, steps_lab, steps_var, size_x_lab, size_x_var,size_y_lab, size_y_var, btn])
box2 = widgets.VBox([prompt_box, neg_prompt_box, img2gen_lab, img2gen_var, steps_lab, steps_var, size_x_lab, size_x_var,size_y_lab, size_y_var, btn])

box2

<Figure size 160x160 with 0 Axes>

In [12]:
out = widgets.Output()
out

Output()

In [13]:
def on_value_change(change):
    prompt = prompt_box.value
    negative_prompt = neg_prompt_box.value
    images_to_generate = int(img2gen_var.value)
    steps = steps_var.value
    width = size_x_var.value
    height = size_y_var.value
    seed = None
    guidance = 7.5 # Higher guidance scale encourages to generate images that are closely linked to the text prompt, usually at the expense of lower image quality.
    with out:
        clear_output(wait=True)
        for _ in range(images_to_generate):
            steps = int(steps)
            width = int(width)
            height = int(height)
            current_seed = seed or torch.randint(0, int(1e5), size=(1, 1))[0].item()
            generator = torch.Generator().manual_seed(int(current_seed))
            img = pipe(prompt=prompt, negative_prompt=negative_prompt, width=width, height=height, num_inference_steps=steps, guidance_scale=guidance, generator=generator).images[0]
            time_now = datetime.datetime.now().strftime("%y.%m.%d_%H:%M:%S")
            plt.imshow(img)
            plt.axis("off")
            print("Current Seed:", current_seed)
            plt.title("")
            plt.show()
         #  img.save(f"./{time_now}_{current_seed}.jpg")

btn.on_click(on_value_change)

